In [1]:
import pandas as pd
import openpyxl
import matplotlib.pyplot as plt
import seaborn as sns
import requests
from urllib.parse import quote
from tqdm import tqdm
import folium
import json

In [2]:
path = '/Users/yniyunj/Desktop/광진구 공모전/'
df_elec1 = pd.read_csv(path + '광진구 전기차 충전소 정보_서울열린데이터광장.csv', encoding='cp949')
# ⚡️ HTML 테이블로 읽기 (엑셀이 아님)
dfs = pd.read_html(path + '충전소 리스트-20250426100518(by.타고).xls')
df_elec2 = dfs[0]  # 첫 번째 테이블 선택
df_elec3 = pd.read_csv(path + '한국환경공단_전기차 충전소 위치 및 운영정보(충전소 ID 포함)_20230531.csv', encoding='cp949')
df_coords = pd.read_csv(path + 'coords_with_address_google.csv', encoding='cp949')

/var/folders/2k/10fc4g4d33q5h9qc2fn4wk6m0000gn/T/ipykernel_5637/4102017270.py:6: DtypeWarning: Columns (11) have mixed types. Specify dtype option on import or set low_memory=False.
  df_elec3 = pd.read_csv(path + '한국환경공단_전기차 충전소 위치 및 운영정보(충전소 ID 포함)_20230531.csv', encoding='cp949')


In [3]:
# ✅ 인증 정보
client_id = '4tayclay5r'
client_secret = '8ANrXhBfqTuXsu5pWdNAAQq2nyVepP9jolAbustp'

# ✅ Geocoding 함수
def geocode_address(address):
    if pd.isna(address) or not isinstance(address, str) or address.strip() == "":
        return None, None

    encoded_address = quote(address)
    url = f'https://maps.apigw.ntruss.com/map-geocode/v2/geocode?query={encoded_address}'

    headers = {
        'X-NCP-APIGW-API-KEY-ID': client_id,
        'X-NCP-APIGW-API-KEY': client_secret,
        'Accept': 'application/json'
    }

    try:
        response = requests.get(url, headers=headers, timeout=3)
        if response.status_code == 200:
            data = response.json()
            if data['addresses']:
                location = data['addresses'][0]
                return location['y'], location['x']
            else:
                return None, None
        else:
            return None, None
    except Exception as e:
        print(f"❌ 요청 실패: {address} - {e}")
        return None, None

# ✅ 위경도 변환 적용
tqdm.pandas()  # 진행률 표시
df_elec1[['위도', '경도']] = df_elec1['주소'].progress_apply(
    lambda x: pd.Series(geocode_address(x))
)
df_elec2[['위도', '경도']] = df_elec2['소재지 도로명 주소'].progress_apply(
    lambda x: pd.Series(geocode_address(x))
)

100%|██████████| 40/40 [00:04<00:00,  8.72it/s]


In [4]:
df_elec1 = df_elec1.drop_duplicates(subset='충전소')
df_elec1.head()

운영기관                        충전소  충전기ID 충전기타입 시설구분(대) 시설구분(소)     지역   시군구  \
0   서울시                    50동부캠퍼스      1  AC완속    공공시설   지자체시설  서울특별시  광진구    
13  서울시  광진구 자양동 거주자우선주차장 가로등형 충전기      1  DC콤보  공동주택시설     아파트  서울특별시  광진구    
14  서울시       어린이대공원 구의문 주차장 복합충전소      1  DC콤보    주차시설   공영주차장  서울특별시  광진구    
20  서울시               어린이대공원 후문주차장      1  DC콤보    주차시설   공영주차장  서울특별시  광진구    
21  서울시        자양우성1차아파트 앞 전기차 충전소      1  DC콤보    주차시설   공영주차장  서울특별시  광진구    

                                                   주소  \
0                      서울특별시 광진구 능동로3길 66-12 50 동부캠퍼스   
13  서울특별시 광진구 자양번영로3길 65 (서울특별시 광진구 뚝섬로36길 39 전기차충...   
14  서울특별시 광진구 능동로 216 (능동, 어린이대공원 구의문공영주차장) 지상1층 진...   
20  서울특별시 광진구 능동로 216 (서울특별시 광진구 천호대로124길 11 전기차충전...   
21    서울특별시 광진구 자양번영로 45 노상공영주차장 유료 42번노상공영주차장 유료 42번   

                            이용가능시간  이용자 제한         충전용량  편의제공  비고          위도  \
0                        24시간 이용가능     NaN    완속(7kW단독)   NaN NaN  37.5348109   
13                       24시간 이용가능     NaN   급속(50kW단독)   NaN NaN  37.5324954   
14                       24시간 이용가능     NaN  급속(200kW동시)   NaN NaN  37.5498986   
20  주중 08:00~19:00, 주말 09:00~18:00     NaN   급속(50kW단독)   NaN NaN  37.5498986   
21                       24시간 이용가능     NaN   급속(50kW단독)   NaN NaN  37.5337203   

             경도  
0   127.0636792  
13  127.0715987  
14  127.0809212  
20  127.0809212  
21  127.0756365

In [5]:
df_elec2 = df_elec2[(~df_elec2['이용가능시간'].str.contains('출입제한', na=False)) & (~df_elec2['충전소 안내'].str.contains('전용', na=False))]
df_elec2 = df_elec2.drop('번호', axis=1).reset_index(drop=True)
df_elec2.head()

충전소명     충전소ID  충전기ID 충전기타입  \
0          어린이대공원 후문주차장  ME174016      1    급속   
1  포르쉐 데스티네이션 그랜드워커힐 서울  CV000752      1    완속   
2  포르쉐 데스티네이션 비스타워커힐 서울  CV000753      1    완속   
3            구의3동 공영주차장  CV000781      1    급속   
4              구의7단지아파트  GN020436      1    완속   

                                 소재지 도로명 주소          위도           경도  \
0                         서울특별시 광진구 능동로 216  37.5498986  127.0809212   
1                        서울특별시 광진구 워커힐로 177  37.5551690  127.1107738   
2                        서울특별시 광진구 워커힐로 177  37.5551690  127.1107738   
3                      서울특별시 광진구 광나루로52길 83  37.5391261  127.0913590   
4  서울특별시 광진구 구의강변로3가길 39(구의동, 구의7단지조합현대아파트)  37.5365108  127.0913924   

      이용가능시간 기관ID    운영기관명  관리업체 전화번호 충전기상태          상태갱신일시     충전기용량  지역코드  \
0  24시간 이용가능   ME      환경부  1661-9408  사용가능  20210124215343  급속(50kW)    11   
1  24시간 이용가능   CV  대영채비(주)  1522-2573  사용가능  20210125000540       NaN    11   
2  24시간 이용가능   CV  대영채비(주)  1522-2573  사용가능  20210125000540       NaN    11   
3  24시간 이용가능   CV  대영채비(주)  1522-2573  사용가능  20210125051629       NaN    11   
4  24시간 이용가능   GN      지엔텔  1544-4279  사용가능  20210124134023       NaN    11   

  주차료무료 여부 충전소 안내  
0       무료    NaN  
1       무료    NaN  
2       무료    NaN  
3       무료    NaN  
4       무료    NaN

In [6]:
df_elec3 = df_elec3[(df_elec3['군구'] == '광진구') & (df_elec3['이용자제한'] == '이용가능')].drop_duplicates()
df_elec3[['위도', '경도']] = df_elec3['위도경도'].str.split(',', expand=True)

df_elec3['위도'] = df_elec3['위도'].astype(float)
df_elec3['경도'] = df_elec3['경도'].astype(float)
df_elec3 = df_elec3.drop('위도경도', axis=1)

In [7]:
df_elec3.head()

설치년도     시도   군구                     주소          충전소명 시설구분(대) 시설구분(소)  \
10     2017  서울특별시  광진구      서울특별시 광진구 능동로 216  어린이대공원 후문주차장    관광시설     관광지   
4554   2020  서울특별시  광진구       서울특별시 광진구 능동로 76      광진문화예술회관    공공시설   지자체시설   
6067   2021  서울특별시  광진구  서울특별시 광진구 뚝섬로52길 74-1  자양2동 유수지 주차장    주차시설   일반주차장   
11410  2024  서울특별시  광진구     서울특별시 광진구 천호대로 670    썬-타워빌딩(광진)  근린생활시설      병원   
27649  2022  서울특별시  광진구      서울특별시 광진구 능동로 400  보건복지행정타운 충전소    공공시설    공공기관   

      기종(대)        기종(소) 운영기관(대)  운영기관(소)        급속충전량            충전기타입 이용자제한  \
10       급속     급속(50kW)     환경부  환경부(협회)     급속(50kW)  DC차데모+AC3상+DC콤보  이용가능   
4554     급속  급속(200kW동시)     환경부  환경부(협회)  급속(200kW동시)             DC콤보  이용가능   
6067     급속  급속(100kW단독)     환경부  환경부(협회)  급속(100kW단독)             DC콤보  이용가능   
11410    완속         AC완속     타기관   파킹클라우드          NaN             AC완속  이용가능   
27649    완속         AC완속     타기관   아마노코리아          NaN             AC완속  이용가능   

              위도          경도  
10     37.551507  127.086928  
4554   37.537534  127.070532  
6067   37.529930  127.077100  
11410  37.551090  127.089588  
27649  37.565011  127.084597

In [8]:
# 1. 필요한 열만 선택하고, 열 이름 통일
elec1_selected = df_elec1[['주소', '충전소', '위도', '경도']].rename(columns={'충전소': '충전소명'})
elec2_selected = df_elec2[['소재지 도로명 주소', '충전소명', '위도', '경도']].rename(columns={'소재지 도로명 주소': '주소'})
elec3_selected = df_elec3[['주소', '충전소명', '위도', '경도']]

# 2. 세 개를 행 방향으로 붙이기 (concat)
df_elec = pd.concat([elec1_selected, elec2_selected, elec3_selected], ignore_index=True)
df_elec = df_elec.sort_values(by='주소', ignore_index=True)
df_elec = df_elec.drop_duplicates()
# 위도, 경도 컬럼을 소수점 7자리로 반올림
df_elec['위도'] = df_elec['위도'].round(7)
df_elec['경도'] = df_elec['경도'].round(7)

df_elec.to_csv(path + '최종광진구전기차충전소-주소-충전소명-위도-경도.csv')
# 결과 확인
df_elec.head()

주소           충전소명          위도           경도
0      서울 광진구 천호대로 666     그랜드파크 오피스텔   37.551356   127.089346
1    서울특별시 광진구 강변역로 17  서울시 구의3동 주민센터  37.5379468  127.0921464
2   서울특별시 광진구 강변역로 17   서울시 구의3동 주민센터   37.537993   127.091984
3     서울특별시 광진구 강변역로 2        서울광진우체국    37.53691   127.089693
4  서울특별시 광진구 강변역로4길 56       광진해모로리버뷰   37.533358   127.092118

In [9]:
df_coords = pd.read_csv(path + 'coords_with_address_google.csv', encoding='cp949')

불가_리스트 = ['사유지', '외국인, 외국공공기관', '개인', '법인']
가능_리스트 = ['시, 도유지', '국유지', '군유지']

df_coords['가능여부'] = df_coords['A8'].apply(
    lambda x: 'X' if x in 불가_리스트 else 'O'
)

In [10]:
df_coords

Y           X    id       gid  lst_rank  \
0   37.544607  127.100963    80  다사647495         2   
1   37.552708  127.097523   168  다사644504         2   
2   37.540078  127.094195   176  다사641490         2   
3   37.538286  127.097601   304  다사644488         2   
4   37.558112  127.096362  1176  다사643510         2   
..        ...         ...   ...       ...       ...   
60  37.536453  127.088556  1649  다사636486         2   
61  37.565299  127.089529  1698  다사637518         2   
62  37.551807  127.097528  1791  다사644503         1   
63  37.540014  127.076085  1806  다사625490         2   
64  37.537354  127.088551  1808  다사636487         2   

                       address      A8 가능여부  
0     대한민국 서울특별시 광진구 광장동 577-1     사유지    X  
1      대한민국 서울특별시 광진구 구의동 4-21  시, 도유지    O  
2    대한민국 서울특별시 광진구 구의동 199-18  시, 도유지    O  
3     대한민국 서울특별시 광진구 구의동 631-1     사유지    X  
4   대한민국 서울특별시 광진구 중곡동 143-138     사유지    X  
..                         ...     ...  ...  
60   대한민국 서울특별시 광진구 자양동 680-64      법인    X  
61   대한민국 서울특별시 광진구 중곡동 176-78      법인    X  
62     대한민국 서울특별시 광진구 구의동 4-14  시, 도유지    O  
63    대한민국 서울특별시 광진구 화양동 360-2      법인    X  
64   대한민국 서울특별시 광진구 자양동 680-63      법인    X  

[65 rows x 8 columns]

In [11]:
# 지도 시작 지점 설정 (광진구 평균 좌표)
map_center = [df_coords['Y'].mean(), df_coords['X'].mean()]
m = folium.Map(location=map_center, zoom_start=15)

with open(path + '서울_자치구_경계_2017.geojson', encoding='utf-8') as f:
    boundary = json.load(f)

# GeoJson으로 지도에 추가
folium.GeoJson(
    boundary,
    name='광진구 경계',
    style_function=lambda x: {
        'fillColor': 'none',      # 내부 채우지 않고
        'color': 'black',         # 외곽선 색
        'weight': 2,              # 선 두께
        'opacity': 0.8
    }
).add_to(m)

# df_coords 빨강/파랑 표시
for idx, row in df_coords.iterrows():
    if row['A8'] in 불가_리스트:
        color = 'black'
        radius = 3   # 불가(빨강)은 작게
    else:
        color = 'blue'
        radius = 10   # 가능(파랑)은 크게
    
    folium.CircleMarker(
        location=[row['Y'], row['X']],
        radius=radius,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7,
        popup=row['address'],
        tooltip=row['A8']
    ).add_to(m)

# df_elec1 초록색 표시
for idx, row in df_elec.iterrows():
    folium.Marker(
        location=[row['위도'], row['경도']],
        icon=folium.Icon(icon='charging-station', prefix='fa', color='blue'),  # 'car'는 FontAwesome 아이콘
        popup=row['충전소명'],
        tooltip=row['충전소명']
    ).add_to(m)

m

In [12]:
# 예시 (df_coords나 df_elec1/2/3 중 하나에서)
point1 = df_coords[df_coords['address'].str.contains('구의동 199-18', na=False)].iloc[0]
point2 = df_elec3[df_elec3['충전소명'].str.contains('구의삼성쉐르빌상가', na=False)].iloc[0]

lat1, lon1 = point1['Y'], point1['X']
lat2, lon2 = point2['위도'], point2['경도']

from math import radians, cos, sin, asin, sqrt

def haversine(lat1, lon1, lat2, lon2):
    R = 6371000  # 지구 반지름 (m)
    lat1, lon1, lat2, lon2 = map(lambda x: radians(float(x)), [lat1, lon1, lat2, lon2])
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a))
    return R * c

# 거리 계산
distance = haversine(lat1, lon1, lat2, lon2)
print(f"두 지점 사이 거리: {distance:.2f} 미터")


두 지점 사이 거리: 39.48 미터


In [13]:
from math import radians, cos, sin, asin, sqrt

# haversine 거리 계산 함수 (미터 단위 반환)
def haversine(lat1, lon1, lat2, lon2):
    R = 6371000  # 지구 반지름 (단위: m)
    lat1, lon1, lat2, lon2 = map(lambda x: radians(float(x)), [lat1, lon1, lat2, lon2])
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a))
    return R * c

# 지도 시작 지점 설정
map_center = [df_coords['Y'].mean(), df_coords['X'].mean()]
m = folium.Map(location=map_center, zoom_start=15)

# 광진구 경계 추가
with open(path + '서울_자치구_경계_2017.geojson', encoding='utf-8') as f:
    boundary = json.load(f)

folium.GeoJson(
    boundary,
    name='광진구 경계',
    style_function=lambda x: {
        'fillColor': 'none',
        'color': 'black',
        'weight': 2,
        'opacity': 0.8
    }
).add_to(m)

for idx, row in df_coords.iterrows():
    lat, lon = row['Y'], row['X']
    
    if row['가능여부'] == 'O':
        # 50m 안에 충전소 있는지 확인
        close = False
        for i, charger in df_elec.iterrows():
            charger_lat, charger_lon = charger['위도'], charger['경도']
            distance = haversine(lat, lon, charger_lat, charger_lon)
            if distance <= 50:
                close = True
                break
        
        if close:
            color = 'blue'
            tooltip_text = "근방에 전기차 충전소 있음. 사용가능"
        else:
            color = 'red'
            tooltip_text = "근방에 전기차 충전소 없음. 전기차 충전소 설치하여 비용 절감 가능"
        
        radius = 10

    else:
        color = 'black'
        radius = 3
        tooltip_text = "설치 불가 부지"

    folium.CircleMarker(
        location=[lat, lon],
        radius=radius,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7,
        tooltip=tooltip_text  # <-- popup 대신 tooltip만 쓴다
    ).add_to(m)

# df_elec 충전소 위치 초록색 표시
for idx, row in df_elec.iterrows():
    folium.Marker(
        location=[row['위도'], row['경도']],
        icon=folium.Icon(icon='charging-station', prefix='fa', color='green'),
        popup=row['충전소명'],
        tooltip=row['충전소명']
    ).add_to(m)

# 지도 출력
m

In [14]:
# m.save(path +'map.html')

In [15]:
# 먼저 color 컬럼을 기본값 'black'으로 초기화
df_coords['elec_charger'] = '-'

# df_coords 반복하면서 color를 조건에 따라 업데이트
for idx, row in df_coords.iterrows():
    lat, lon = row['Y'], row['X']
    
    if row['가능여부'] == 'O':
        close = False
        for i, charger in df_elec.iterrows():
            charger_lat, charger_lon = charger['위도'], charger['경도']
            distance = haversine(lat, lon, charger_lat, charger_lon)
            if distance <= 50:
                close = True
                break
        
        if close:
            df_coords.at[idx, 'elec_charger'] = 'O'
        else:
            df_coords.at[idx, 'elec_charger'] = 'X'
    else:
        df_coords.at[idx, 'elec_charger'] = '-'  # 설치 불가 부지는 검정색 유지

df_coords

Y           X    id       gid  lst_rank  \
0   37.544607  127.100963    80  다사647495         2   
1   37.552708  127.097523   168  다사644504         2   
2   37.540078  127.094195   176  다사641490         2   
3   37.538286  127.097601   304  다사644488         2   
4   37.558112  127.096362  1176  다사643510         2   
..        ...         ...   ...       ...       ...   
60  37.536453  127.088556  1649  다사636486         2   
61  37.565299  127.089529  1698  다사637518         2   
62  37.551807  127.097528  1791  다사644503         1   
63  37.540014  127.076085  1806  다사625490         2   
64  37.537354  127.088551  1808  다사636487         2   

                       address      A8 가능여부 elec_charger  
0     대한민국 서울특별시 광진구 광장동 577-1     사유지    X            -  
1      대한민국 서울특별시 광진구 구의동 4-21  시, 도유지    O            X  
2    대한민국 서울특별시 광진구 구의동 199-18  시, 도유지    O            O  
3     대한민국 서울특별시 광진구 구의동 631-1     사유지    X            -  
4   대한민국 서울특별시 광진구 중곡동 143-138     사유지    X            -  
..                         ...     ...  ...          ...  
60   대한민국 서울특별시 광진구 자양동 680-64      법인    X            -  
61   대한민국 서울특별시 광진구 중곡동 176-78      법인    X            -  
62     대한민국 서울특별시 광진구 구의동 4-14  시, 도유지    O            X  
63    대한민국 서울특별시 광진구 화양동 360-2      법인    X            -  
64   대한민국 서울특별시 광진구 자양동 680-63      법인    X            -  

[65 rows x 9 columns]

In [16]:
# color가 red 또는 blue인 것만 추출
df_available = df_coords[(df_coords['elec_charger'] == 'O') | (df_coords['elec_charger'] == 'X')].reset_index(drop=True)

# df_available.to_csv(path + '')
df_available[['Y', 'X', 'id', 'gid', 'lst_rank', 'address', 'A8', 'elec_charger']]

Y           X    id       gid  lst_rank  \
0   37.552708  127.097523   168  다사644504         2   
1   37.540078  127.094195   176  다사641490         2   
2   37.537366  127.091946  1032  다사639487         2   
3   37.533676  127.068197   215  다사618483         2   
4   37.546315  127.073785   245  다사623497         2   
5   37.535563  127.091956   423  다사639485         2   
6   37.567102  127.089519   517  다사637520         2   
7   37.539088  127.069298   645  다사619489         1   
8   37.539993  127.070425   885  다사620490         2   
9   37.545438  127.080582   992  다사629496         1   
10  37.545442  127.081714  1127  다사630496         2   
11  37.539100  127.072694  1464  다사622489         2   
12  37.552712  127.098655  1532  다사645504         2   
13  37.545509  127.100958  1626  다사647496         2   
14  37.539092  127.070430  1691  다사620489         2   
15  37.564398  127.089534  1152  다사637517         2   
16  37.566201  127.089524  1306  다사637519         2   
17  37.551810  127.098660  1414  다사645503         2   
18  37.551807  127.097528  1791  다사644503         1   

                           address      A8 elec_charger  
0          대한민국 서울특별시 광진구 구의동 4-21  시, 도유지            X  
1        대한민국 서울특별시 광진구 구의동 199-18  시, 도유지            O  
2   대한민국 서울특별시 광진구 구의제3동 강변역로2길 18  시, 도유지            X  
3         대한민국 서울특별시 광진구 자양동 855-1     국유지            X  
4       대한민국 서울특별시 광진구 화양동 111-265  시, 도유지            X  
5        대한민국 서울특별시 광진구 구의동 587-64  시, 도유지            O  
6        대한민국 서울특별시 광진구 중곡동 176-47  시, 도유지            X  
7          대한민국 서울특별시 광진구 자양동 2-21     국유지            X  
8          대한민국 서울특별시 광진구 화양동 6-12     군유지            X  
9         대한민국 서울특별시 광진구 화양동 302-2     국유지            X  
10    대한민국 서울특별시 광진구 광나루로 474, 507  시, 도유지            X  
11       대한민국 서울특별시 광진구 자양동 227-10  시, 도유지            X  
12         대한민국 서울특별시 광진구 구의동 4-19  시, 도유지            X  
13         대한민국 서울특별시 광진구 천호대로 788     군유지            O  
14                대한민국 서울특별시 광진구의회     군유지            X  
15       대한민국 서울특별시 광진구 중곡동 176-60  시, 도유지            X  
16       대한민국 서울특별시 광진구 용마산로22길 76  시, 도유지            X  
17       대한민국 서울특별시 광진구 광장동 381-80  시, 도유지            X  
18         대한민국 서울특별시 광진구 구의동 4-14  시, 도유지            X

In [17]:
df_available.to_csv(path + 'coords_with_address_google_국시도유지_전기차충전기여부.csv')

In [18]:
import geopandas as gpd

# Shapefile 읽기
gdf = gpd.read_file(path + 'sorting/sorting.shp')

print(gdf.head())

  OPERT_DE  RW_SN SIG_CD  12      id       gid       lst  pop_scaled  \
0     None      1  11110 NaN   168.0  다사644504  1.042267   -0.771649   
1     None      1  11110 NaN   176.0  다사641490  1.728635   -0.697309   
2     None      1  11110 NaN  1032.0  다사639487  1.475816   -0.771649   
3     None      1  11110 NaN   215.0  다사618483  1.826932    0.244334   
4     None      1  11110 NaN   245.0  다사623497  1.870313    0.723416   

   ndvi_scale  ndwi_scale  dem_scaled  road_area_  vol_scaled  speed_scal  \
0   -0.229495    0.287660    2.064985   -1.006160   -0.833822   -0.487541   
1   -0.769680    0.832995   -0.261458    1.417163   -0.595254   -0.887795   
2   -0.997127    1.004343   -0.336093   -0.023071   -0.657330   -0.311598   
3   -0.691102    0.449827   -0.583655    1.777258    0.153446    0.472436   
4   -0.869487    0.858902   -0.312153    1.271256    0.156114   -0.192454   

   lst_rank                                           geometry  
0       2.0  POLYGON ((964406.331 19504

In [19]:
# SIG_CD를 구 이름으로 매핑
sig_cd_to_gu = {
    '11110': '광진구',
    # 필요하면 다른 구 코드도 추가 가능
}

# SIG_CD를 문자열로 맞춰주고
gdf['SIG_CD'] = gdf['SIG_CD'].astype(str)

# 새로운 'gu_name' 컬럼 추가
gdf['gu_name'] = gdf['SIG_CD'].map(sig_cd_to_gu)

In [20]:
from math import radians, cos, sin, asin, sqrt

# haversine 거리 계산 함수 (미터 단위 반환)
def haversine(lat1, lon1, lat2, lon2):
    R = 6371000  # 지구 반지름 (단위: m)
    lat1, lon1, lat2, lon2 = map(lambda x: radians(float(x)), [lat1, lon1, lat2, lon2])
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a))
    return R * c

# 지도 시작 지점 설정
map_center = [df_coords['Y'].mean(), df_coords['X'].mean()]
m = folium.Map(location=map_center,
               zoom_start = 15,
               tiles = 'CartoDB positron'
               # tile_list = [
                #    'OpenStreetMap',
                #    'Stamen Terrain',
                #    'Stamen Toner',
                #    'Stamen Watercolor',
                #    'CartoDB positron',
                #    'CartoDB dark_matter',
                #    'Esri WorldImagery'
                # ]
               )

# 광진구 경계 추가
with open(path + '서울_자치구_경계_2017.geojson', encoding='utf-8') as f:
    boundary = json.load(f)

folium.GeoJson(
    boundary,
    name='광진구 경계',
    style_function=lambda x: {
        'fillColor': 'none',
        'color': 'black',
        'weight': 2,
        'opacity': 0.8
    }
).add_to(m)

for idx, row in df_coords.iterrows():
    lat, lon = row['Y'], row['X']
    
    if row['가능여부'] == 'O':
        # 50m 안에 충전소 있는지 확인
        close = False
        for i, charger in df_elec.iterrows():
            charger_lat, charger_lon = charger['위도'], charger['경도']
            distance = haversine(lat, lon, charger_lat, charger_lon)
            if distance <= 50:
                close = True
                break
        
        if close:
            color = 'blue'
            tooltip_text = "근방에 전기차 충전소 있음. 사용가능"
        else:
            color = 'red'
            tooltip_text = "근방에 전기차 충전소 없음. 전기차 충전소 설치하여 비용 절감 가능"
        
        radius = 10

    else:
        color = 'black'
        radius = 3
        tooltip_text = "설치 불가 부지"

    folium.CircleMarker(
        location=[lat, lon],
        radius=radius,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7,
        tooltip=tooltip_text  # <-- popup 대신 tooltip만 쓴다
    ).add_to(m)

# df_elec 충전소 위치 초록색 표시
for idx, row in df_elec.iterrows():
    folium.Marker(
        location=[row['위도'], row['경도']],
        icon=folium.Icon(icon='charging-station', prefix='fa', color='green'),
        popup=row['충전소명'],
        tooltip=row['충전소명']
    ).add_to(m)

folium.GeoJson(
    gdf,
    name='폴리곤 레이어',
    style_function=lambda x: {
        'fillColor': 'blue',
        'color': 'black',
        'weight': 2,
        'fillOpacity': 0.2
    },
    tooltip=folium.GeoJsonTooltip(
        fields=['gid'],             # 표시할 필드
        aliases=['GID 값:'],        # 툴팁에 나올 라벨명
        localize=True
    )
).add_to(m)

# 지도 출력
m

In [22]:
m.save(path +'250430-map.html')